# hola
* adios
    
    * bueno
        * ahhh

Para crear el ambiente corremos en la terminal:
``` bash
conda create --name Ngram python=3.8.19
```

%pip install numpy
%pip install scipy
%pip install cython
%pip install gensim
%pip install chardet

In [2]:
##year_1 and year_2 comprise the time period of ngrams to read##

import numpy
import scipy
import cython
import gensim
from gensim import models, similarities
import logging
import os
import re
import sys  
import itertools
import math


In [9]:
import os
import itertools
import gensim
import logging
import numpy

# Setup logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

class MySentences(object):
    def __init__(self, dirname, start_year, end_year, limit=None):
        self.dirname = dirname
        self.start_year = start_year
        self.end_year = end_year
        self.limit = limit

    def __iter__(self):
        for fname in os.listdir(self.dirname):
            with gensim.utils.open(os.path.join(self.dirname, fname)) as fin:
                for line in itertools.islice(fin, self.limit):
                    line = gensim.utils.to_unicode(line).split("\t")
                    if len(line) < 3:
                        continue
                    ngram = line[0]
                    try:
                        year = int(line[1])
                    except ValueError:
                        continue
                    match_count = int(line[2])
                    if year < self.start_year or year > self.end_year:
                        continue
                    processed_ngram = [word.split("_")[0] for word in ngram.lower().split()]
                    for x in range(match_count):
                        yield processed_ngram

# Define year_1 and year_2
year_1 = 2000
year_2 = 2010

# Create sentences iterator
sentences = MySentences("./ngrams", year_1, year_2)

# Build the vocabulary
model = gensim.models.word2vec.Word2Vec(vector_size=300, window=5, min_count=10, workers=10, hs=0, negative=8)
model.build_vocab(sentences)


2024-04-17 04:06:04,197 : INFO : Word2Vec lifecycle event {'params': 'Word2Vec<vocab=0, vector_size=300, alpha=0.025>', 'datetime': '2024-04-17T04:06:04.197484', 'gensim': '4.3.2', 'python': '3.8.19 (default, Mar 20 2024, 19:55:45) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.22621-SP0', 'event': 'created'}
2024-04-17 04:06:04,198 : INFO : collecting all words and their counts
2024-04-17 04:06:04,212 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2024-04-17 04:06:04,235 : INFO : PROGRESS: at sentence #10000, processed 50000 words, keeping 300 word types
2024-04-17 04:06:04,262 : INFO : PROGRESS: at sentence #20000, processed 100000 words, keeping 705 word types
2024-04-17 04:06:04,296 : INFO : PROGRESS: at sentence #30000, processed 150000 words, keeping 1121 word types
2024-04-17 04:06:04,323 : INFO : PROGRESS: at sentence #40000, processed 200000 words, keeping 1410 word types
2024-04-17 04:06:04,346 : INFO : PROGRESS: at sentence #50000, pro

In [ ]:
# Check if vocabulary is built
if len(model.wv):
    logging.info("Vocabulary built successfully!")
    # Train word2vec model
    model.train(sentences, total_examples=model.corpus_count, epochs=model.epochs)
    logging.info("Model trained successfully!")
else:
    logging.error("Vocabulary is empty. Check your data and filters.")

2024-04-17 04:21:46,544 : INFO : Vocabulary built successfully!
2024-04-17 04:21:46,545 : INFO : Word2Vec lifecycle event {'msg': 'training model with 10 workers on 92628 vocabulary and 300 features, using sg=0 hs=0 sample=0.001 negative=8 window=5 shrink_windows=True', 'datetime': '2024-04-17T04:21:46.545323', 'gensim': '4.3.2', 'python': '3.8.19 (default, Mar 20 2024, 19:55:45) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.22621-SP0', 'event': 'train'}
2024-04-17 04:21:47,561 : INFO : EPOCH 0 - PROGRESS: at 0.07% examples, 661757 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:21:48,563 : INFO : EPOCH 0 - PROGRESS: at 0.13% examples, 637284 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:21:49,567 : INFO : EPOCH 0 - PROGRESS: at 0.21% examples, 677390 words/s, in_qsize 0, out_qsize 1
2024-04-17 04:21:50,571 : INFO : EPOCH 0 - PROGRESS: at 0.28% examples, 697379 words/s, in_qsize 0, out_qsize 1
2024-04-17 04:21:51,574 : INFO : EPOCH 0 - PROGRESS: at 0.36% examples, 701323 w

In [11]:

# Train word2vec model
model.train(sentences, total_examples=model.corpus_count, epochs=model.epochs)

# Save the model
model.save('w2vmodel_ng5_'+str(year_1)+'_'+str(year_2)+'_full')

# Save the vectors
numpy.savetxt('syn0_ngf_'+str(year_1)+'_'+str(year_2)+'_full.txt', model.wv.vectors, delimiter=" ")

# Save the vocabulary list
vocab_list = model.wv.index_to_key
for i in range(0, len(vocab_list)):
    if vocab_list[i] == '':
        vocab_list[i] = "thisisanemptytoken"+str(i)

with open('vocab_list_ngf_'+str(year_1)+'_'+str(year_2)+'_full.txt', 'wb') as outfile:
    for i in range(0, len(vocab_list)):
        outfile.write(vocab_list[i].encode('utf8')+"\n".encode('ascii'))


2024-04-17 04:31:40,089 : WARNING : Effective 'alpha' higher than previous training cycles
2024-04-17 04:31:40,090 : INFO : Word2Vec lifecycle event {'msg': 'training model with 10 workers on 92628 vocabulary and 300 features, using sg=0 hs=0 sample=0.001 negative=8 window=5 shrink_windows=True', 'datetime': '2024-04-17T04:31:40.090409', 'gensim': '4.3.2', 'python': '3.8.19 (default, Mar 20 2024, 19:55:45) [MSC v.1916 64 bit (AMD64)]', 'platform': 'Windows-10-10.0.22621-SP0', 'event': 'train'}
2024-04-17 04:31:41,096 : INFO : EPOCH 0 - PROGRESS: at 0.08% examples, 744544 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:31:42,098 : INFO : EPOCH 0 - PROGRESS: at 0.15% examples, 754198 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:31:43,104 : INFO : EPOCH 0 - PROGRESS: at 0.24% examples, 765608 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:31:44,109 : INFO : EPOCH 0 - PROGRESS: at 0.32% examples, 768732 words/s, in_qsize 0, out_qsize 0
2024-04-17 04:31:45,111 : INFO : EPOCH 0 - PROGRESS: 